In [1]:
! pip install openstef==3.4.7

  Using cached pandas-2.1.3-cp310-cp310-win_amd64.whl.metadata (18 kB)
Using cached pandas-2.1.3-cp310-cp310-win_amd64.whl (10.7 MB)
  Attempting uninstall: pandas
    Found existing installation: pandas 1.5.3
    Uninstalling pandas-1.5.3:
      Successfully uninstalled pandas-1.5.3


  You can safely remove it manually.


In Google Collab, the pandas version has to be set to 1.5.3 due to compatability reasons. 

In [2]:
! pip install pandas==1.5.3

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
openstef 3.4.7 requires pandas==2.1.3, but you have pandas 1.5.3 which is incompatible.



  Using cached pandas-1.5.3-cp310-cp310-win_amd64.whl.metadata (12 kB)
Using cached pandas-1.5.3-cp310-cp310-win_amd64.whl (10.4 MB)
  Attempting uninstall: pandas
    Found existing installation: pandas 2.1.3
    Uninstalling pandas-2.1.3:
      Successfully uninstalled pandas-2.1.3


# Workshop part 3 | Learn how to perform a backtest
In the third part of this workshop, we will perform a backtest for the same location as the first two parts.

The learning points are:
- What a backtest is and how it works on a high level;
- Hands on experience with evaluating a model using a backtest;
- Being able to understand the results of a backtest.

A backtest is the evaluation of the model on historical data. Essentially, it is a way of testing how OpenSTEF would have performed if it had been used in the past. 

In [3]:
import pandas as pd 
import openstef
from openstef.data_classes.model_specifications import ModelSpecificationDataClass
from openstef.data_classes.prediction_job import PredictionJobDataClass 
from openstef.pipeline.train_create_forecast_backtest import train_model_and_forecast_back_test
import openstef.metrics.metrics as openstef_metrics

# Set plotly as the default pandas plotting backend.
pd.options.plotting.backend = 'plotly'

c:\Users\AL28793\AppData\Local\anaconda3\envs\openstef-workshop\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


2024-02-19 09:20:58 [info     ] Proloaf not available, setting constructor to None


## Define the prediction job
The same as in workshop parts 1 and 2, a prediction job has to be defined. As we are making a backtest for same location, we can use the exact same prediction job. 

In [4]:
# Define properties of training/prediction. We call this a 'prediction_job'. The same is used as in the first exercise.
pj = dict(id=287,
        model='xgb', 
        quantiles=[0.10,0.30,0.50,0.70,0.90],
        forecast_type="demand", 
        lat=52.0,
        lon=5.0,
        horizon_minutes=0.25,
        resolution_minutes=15,
        name="workshop_exercise_3",
        save_train_forecasts=True,
       )

pj=PredictionJobDataClass(**pj)
modelspecs = ModelSpecificationDataClass(id=pj['id'])

If you are working with Google Collab, just upload the data in the 'Files' section on Google Collab. You can find this at the left toolbar, the fifth item from the top. 

If you are working with another program, please alter the path below to upload the correct data.

In [5]:
input_data=pd.read_csv("/content/input_data_sun_heavy.csv", index_col=0, parse_dates=True)

# Uncomment this line if you are not working with Google Colab but on your own device
# input_data=pd.read_csv("../data/input_data_sun_heavy.csv", index_col=0, parse_dates=True)

## Perform the backtest
The prediction job and input data have been provided above, so now a backtest can be performed. 

As you can see, one of the inputs of the pipeline is 'training_horizons', which is set to 0.25 and 47.0. This means that the backtest is made predicting both 0.25 hours (which is 15 minutes) and 47 hours into the future. 

Exercise: 
- How many pipelines do you need to train a model and make a backtest? 

In [6]:
n_folds=1

forecast, model, train_data, validation_data, test_data = openstef.pipeline.train_create_forecast_backtest.train_model_and_forecast_back_test(
    pj,
    modelspecs = modelspecs,
    input_data = input_data,
    training_horizons=[0.25, 47.0],
    n_folds=n_folds,
 )

2024-02-19 09:20:59 [info     ] Found 22 values of constant load (repeated values), converted to NaN value. cleansing_step=repeated_values frac_values=0.0006278359635855141 num_values=22 pj_id=287
2024-02-19 09:20:59 [info     ] Removed 22 NaN values          num_removed_values=22
2024-02-19 09:21:05 [info     ] Postproces in preparation of storing


## Evaluate the results 
Below, the results from the backtest are plotted. With these plots, answer the questions of the exercise below. 

Exercise: answer the following questions: 
- When is the model uncertain? Why? 
- What difference do you see between the horizons? 

Bonus: look at the differences between the two time horizons using metrics. You can use the build-in metrics package of OpenSTEF. See the documentation website [here](https://openstef.github.io/openstef/openstef.metrics.html) . For example, look at the differnce in mean absolute error under the plot below. 


In [7]:
for horizon in set(forecast.horizon):
    fig = forecast.loc[forecast.horizon==horizon,['quantile_P10','quantile_P30',
                    'quantile_P50','quantile_P70','quantile_P90','realised','forecast']].plot(
                                                                                   title=f"Horizon: {horizon}")
    fig.update_traces(
         line=dict(color="green", width=1), fill='tonexty', fillcolor='rgba(0, 255, 0, 0.1)',
         selector=lambda x: 'quantile' in x.name and x.name != 'quantile_P10')
    fig.update_traces(
         line=dict(color="green", width=1),
         selector=lambda x: 'quantile_P10' == x.name)
    fig.update_traces(
         line=dict(color="red", width=2),
         selector=lambda x: 'realised' in x.name)
    fig.update_traces(
         line=dict(color="blue", width=2),
         selector=lambda x: 'forecast' in x.name)
    fig.show()

In [8]:

for horizon in set(forecast.horizon):
     mean_absolute_error=openstef_metrics.mae(forecast.loc[forecast.horizon==horizon, 'realised'], forecast.loc[forecast.horizon==horizon, 'forecast'])
     print(horizon, mean_absolute_error)


0.25 0.1868751239322968
47.0 0.3399205071164553
